# Лабораторная работа №6
Выполняли:


1.   Алексеев Михаил Николаевич
2.   Гурьянов Марк Владимирович
3.   Ермаков Михаил Константинович
4.   Карандашева Надежда Алексеевна
5.   Юсупова Эдна Эдуардовна

In [ ]:
import os
import re
import pandas as pd
import numpy as np
from statistics import mean
from datetime import datetime
from scipy import interpolate
from scipy.fft import rfft, fftfreq, irfft


import plotly
import plotly.io as pio
import plotly.graph_objs as go
from plotly.subplots import make_subplots
from plotly.offline import download_plotlyjs, init_notebook_mode, iplot, plot

init_notebook_mode(connected=True)
pio.renderers.default = "colab"
pd.set_option("precision", 4)

# Скачиваем данные

In [ ]:
data_dir = '/content/data'
if not (os.path.exists(data_dir) and len(os.listdir(data_dir)) == 6):
  print('========= Downloading data ... =========')
  link = 'https://www.dropbox.com/s/xv7n1txkxvsigis/lab6_data.zip?dl=0'
  os.system('wget ' + link + ' -O ' + data_dir + '.zip')
  os.system('unzip ' + data_dir + '.zip' + ' -d ' + data_dir)
  os.system('rm ' + data_dir + '.zip')
  os.system('rm -R ' + data_dir + '/__MACOSX')
  print('=========       Success        =========')
else:
  print('========= Data is already dowloaded =========')
print('Загруженные файлы:')  
print(' '.join([name for name in os.listdir(data_dir)]))

========= Downloading data ... =========
=========       Success        =========
Загруженные файлы:
music.txt calm.txt game.txt prog.txt math.txt


## Описание данных

*   **calm.txt** - Пассивное бодрствование
*   **music.txt** - Пассивное бодрствование с прослушиванием спокойной музыки
*   **math.txt** - Решение мат задач
*   **prog.txt** - Решение задач с программированием
*   **game.txt** - Игра на ПК

# Вспомогательные функции

In [ ]:
def moving_average(data, n):
  a = [data[0]] * (n // 2) + list(data) + [data[-1]] * (n // 2)
  ret = np.cumsum(a, dtype=float)
  ret[n:] = ret[n:] - ret[:-n]
  return ret[n:] / n

In [ ]:
def moving_average_amplitude(data, n):
  h = n // 2
  a = [data[0]] * h + list(data) + [data[-1]] * h
  abs_a = list(np.abs(a))
  ampl = [0] * len(data)
  ampl[0] = max([abs_a[i] for i in range(-h, h)])
  maxj = abs_a.index(ampl[0])
  for j in range(0, len(data)):
    if abs_a[j + h] > abs_a[maxj]:
      maxj = j + h
    if maxj < j - n:
      ampl[j] = max([abs_a[i] for i in range(j - h, j + h)])
      maxj = abs_a.index(ampl[j])
    else:
      ampl[j] = abs_a[maxj]
  return ampl

In [ ]:
def time_formating(df):
  time = df['time']
  time = (time - time.iloc[0]).to_list() 
  i = 0
  t = []
  delta = 0.05
  while i < len(time):
    j = i
    while time[j] - time[i] < delta:
      j += 1
      if j == len(time):
        t.extend(np.linspace(time[i], time[-1] + 0.5, j - i + 1)[:-1])
        break
    if j < len(time):
      t.extend(np.linspace(time[i], time[j], j - i + 1)[:-1])
    i = j
  df['time'] = t
  return df

# Чтение данных

Данный метод считывает и нормализует данные \\
Реализация позволяет без труда скормить данные с 16 каналами и дальнейшая обработка пройдет успешно \\
Также в случае если есть "битые" данные можно передать в метод название испорченых каналов чтобы на этапе чтения убрать эти данные

In [ ]:
def get_dataframe_from_txt_and_normalize(path, *dropped_list):
  with open(path, 'r') as f:
    SAMPLE_RATE = int(re.findall(r'-?\d+\.?\d*', f.readlines()[2])[0])

  # Читаем данные в dataframe
  df = pd.read_csv(path, skiprows=list(range(4)), delimiter=',')

  selected_index = []
  for i in range(len(df.columns)):
    if 'EXG Channel' in df.columns[i] or 'Timestamp (Formatted)' in df.columns[i]:
      selected_index.append(i)
  # Делаем выборку по нужным столбцам
  df = df.iloc[:, selected_index]

  # Меняем название столбца времени и приводим данные в нужный формат
  channel_names = [name.lstrip() for name in df.columns if name.lstrip() != 'Timestamp (Formatted)']
  df.columns = channel_names + ['time']
  df['time'] = df['time'].apply(lambda x: datetime.strptime(x.lstrip(), '%Y-%m-%d %H:%M:%S.%f').timestamp())
  # Находим максимум и минимум в столбце времени и убираем по 10 секунд в начале и в конце считаных данных
  min_t = df['time'].min()
  max_t = df['time'].max()

  # Стираем по 5 секунд в начале и в конце чтобы осеить испорченные данные
  df = df.loc[(df['time'] > min_t + 5) & (df['time'] < max_t - 5)]

  # Удаляем испорченный канал
  for channel in list(dropped_list):
    df.drop(channel, inplace=True, axis=1)
    channel_names.remove(channel)

  # Нормализуем данные сигнала
  for channel in channel_names:
    n = 100 
    df[channel]-=moving_average(df[channel].to_list(), n)
    df[channel]/=moving_average_amplitude(df[channel].to_list(), n)

  # Нормализуем данные времени
  df = time_formating(df)

  # Убираем дубликаты по столбцу time
  df = df.drop_duplicates(keep='last', subset=['time'], ignore_index=True)

  return {'df': df, 'channels': channel_names, 'name': path.replace('.txt', '').replace(data_dir + '/', ''), 'SAMPLE_RATE': SAMPLE_RATE}

In [ ]:
input_data_list = [get_dataframe_from_txt_and_normalize(data_dir + '/' + file, 'EXG Channel 2') for file in os.listdir(data_dir) if file != '.ipynb_checkpoints']

## Убедимся, что данные были прочитаны корректно
(если есть испорченные каналы, то добавляем их в  `dropped_list`)

In [ ]:
print(input_data_list[0]['name'])
print(input_data_list[0]['channels'])

music
['EXG Channel 0', 'EXG Channel 1', 'EXG Channel 3', 'EXG Channel 4', 'EXG Channel 5', 'EXG Channel 6', 'EXG Channel 7']


In [ ]:
input_data_list[0]['df']

EXG Channel 0  EXG Channel 1  EXG Channel 3  EXG Channel 4  \
0            -1.0000        -1.0000        -1.0000        -0.4477   
1            -1.0000        -1.0000        -1.0000        -1.0000   
2             0.1280         0.1147         0.0302        -0.2558   
3             1.0000         1.0000         1.0000         0.9727   
4             0.8246         0.8316         0.8681         1.0000   
...              ...            ...            ...            ...   
13422        -0.9077        -0.9042        -0.9006        -0.8335   
13423        -0.8192        -0.8257        -0.8706        -1.0000   
13424         0.1692         0.1628         0.1031        -0.1284   
13425         0.7807         0.7808         0.7533         0.6372   
13426         0.1215         0.1273         0.1354         0.2081   

       EXG Channel 5  EXG Channel 6  EXG Channel 7     time  
0            -1.0000         0.3453        -0.8425   0.0000  
1            -1.0000        -1.0000        -1.0000   0.0022  
2             0.0429        -1.0000        -0.0928   0.0044  
3             1.0000         0.0461         1.0000   0.0066  
4             0.8586         0.8047         0.9412   0.0089  
...              ...            ...            ...      ...  
13422        -0.8986        -0.3356        -0.9024  53.6621  
13423        -0.8567        -1.0000        -0.9517  53.6663  
13424         0.1230        -0.6963         0.0186  53.6705  
13425         0.7649         0.1075         0.7387  53.6746  
13426         0.1359         0.3157         0.1666  53.6788  

[13427 rows x 8 columns]

# Глобальные переменные

In [ ]:
bounds=[
        {'start':0,'end':4, 'name': 'Delta', 'color': 'Turquoise'},   
        {'start':4,'end':8, 'name': 'Theta', 'color': 'PaleTurquoise'},   
        {'start':8,'end':12, 'name': 'Alpha', 'color': 'Turquoise'},  
        {'start':12,'end':30, 'name': 'Beta', 'color': 'PaleTurquoise'}, 
        {'start':30,'end':50, 'name': 'Gamma', 'color': 'Turquoise'}  
       ]

labels=[data['name'] for data in input_data_list]

# Исходные данные

In [ ]:
def draw_data(data, draw_fig = True, save_html=False):
  fig = make_subplots(
      rows=len(data['channels']), cols=1, subplot_titles=(data['channels'])
  )

  for i in range(len(data['channels'])):
    fig.add_trace(
        go.Scatter(
          x=data['df']['time'], y=data['df'][data['channels'][i]], name=data['channels'][i], line = dict(width = 1)
        ), row=i + 1, col=1
    )
    fig.update_layout(title_text=data['name'], height=150 * len(data['channels']), showlegend=False)
  # Для удобства экспортируем график в html
  if save_html:
    plotly.offline.plot(fig, filename=data['name']+'_original_data.html', show_link=True)
  if draw_fig:
    fig.show()

In [ ]:
draw_data(input_data_list[0])

# Обработка данных

## Интерполируем данные

In [ ]:
def interpolation(data):
  DURATION = data['df']['time'].max()  # Секунды
  N = int(data['SAMPLE_RATE'] * DURATION) # Кол-во точек
  time = np.linspace(0, DURATION, N)
  signals = {}
  for j in range(len(data['channels'])):
    value = interpolate.interp1d(data['df']['time'], data['df'][data['channels'][j]].to_numpy(), kind='cubic', fill_value='extrapolate')(time)
    signals[data['channels'][j]] = value

  data['time'] = time 
  data['signals'] = signals 
  data['N'] = N 

## Применяем преобразование Фурье

In [ ]:
def fourie(data):
  interpolation(data)
  N = data['N']

  xf = fftfreq(N, 1/ data['SAMPLE_RATE'])[1:N // 2]
  res = pd.DataFrame({'x': xf})

  for j in range(len(data['channels'])):
    yf = rfft(data['signals'][data['channels'][j]])[1:N // 2]
    # Фильтрация сигнала от электрического шума (шум в диапазоне 50 Гц или 60 Гц)
    for i in range(len(yf)):
      if xf[i] > 50 and xf[i] < 60:
          yf[i] = 0
    res[data['channels'][j]] = pd.Series(2 / N * np.abs(yf))
  
  res.set_index('x', inplace=True)
  data['x'] = xf
  data['y'] = yf
  return res

In [ ]:
fft=[fourie(data) for data in input_data_list]

In [ ]:
fft[0]

EXG Channel 0  EXG Channel 1  EXG Channel 3  EXG Channel 4  \
x                                                                      
0.0186           0.1264         0.1267         0.1254         0.1173   
0.0373           0.1405         0.1409         0.1399         0.1327   
0.0559           0.1476         0.1479         0.1470         0.1404   
0.0745           0.1478         0.1481         0.1471         0.1411   
0.0932           0.1374         0.1377         0.1367         0.1305   
...                 ...            ...            ...            ...   
124.8975         0.0051         0.0051         0.0052         0.0053   
124.9162         0.0049         0.0049         0.0050         0.0050   
124.9348         0.0049         0.0049         0.0049         0.0047   
124.9534         0.0057         0.0057         0.0056         0.0052   
124.9721         0.0068         0.0067         0.0066         0.0059   

          EXG Channel 5  EXG Channel 6  EXG Channel 7  
x                                                      
0.0186           0.1266         0.0598         0.1248  
0.0373           0.1408         0.0734         0.1394  
0.0559           0.1479         0.0804         0.1467  
0.0745           0.1483         0.0826         0.1472  
0.0932           0.1380         0.0767         0.1370  
...                 ...            ...            ...  
124.8975         0.0051         0.0046         0.0052  
124.9162         0.0049         0.0041         0.0050  
124.9348         0.0049         0.0031         0.0049  
124.9534         0.0056         0.0031         0.0054  
124.9721         0.0066         0.0031         0.0063  

[6708 rows x 7 columns]

### Так как визуализировать несколько каналов неудобно найдем максимумы и средние значения

In [ ]:
def aggregate(df):
  res = pd.DataFrame({'x':df.index})
  res.set_index('x', inplace=True)
  res['max'] = df.max(axis=1)
  res['mean'] = df.mean(axis=1)
  return res

In [ ]:
fft_agg=[aggregate(signal) for signal in fft]

## Изобразим график

In [ ]:
def draw_fourie(draw_by='max', draw_fig = True, save_html=False):
  fig = make_subplots(
      rows=len(input_data_list), cols=1, subplot_titles=(labels)
  )

  # Список зоны для каждого графика
  shapes = []

  for i in range(len(fft_agg)):
    # Преобразуем комплексные числа
    max_y = fft_agg[i]['max'][fft_agg[i].index < 45].max()
    df = pd.DataFrame({'x': fft_agg[i].index, 'y': fft_agg[i][draw_by]})
    fig.add_trace(
        go.Scatter(
          x=df.x, y=df.y, name="EEG", line = dict(width = 1)
        ), row=i + 1, col=1
    )

    # Название зон 
    text_trace = go.Scatter(
        x=[2, 6, 10, 21, 40],
        y=[max_y] * 5,
        text=[bound['name'] for bound in bounds],
        mode="text",
    )
    fig.add_trace(
        text_trace, row=i + 1, col=1
    )
    fig.update_xaxes(range=[0,50], row=i + 1, col=1)
    fig.update_yaxes(range=[0, max_y + 0.01], row=i + 1, col=1)
    # Создаём зоны
    for k in range(len(bounds)):
      shapes.append(
          dict(
              type="rect", 
              y0=0, y1=0.7,
              x0=bounds[k]['start'], x1=bounds[k]['end'],
              xref="x" + str(i + 1), yref="y" + str(i + 1), 
              fillcolor=bounds[k]['color'], opacity=0.4, line_width=0, layer="below"
          )
      )

  fig.update_layout(title_text=f"Fourie data(drow by {draw_by})", height=len(input_data_list) * 150, shapes=shapes, showlegend=False)
  
  # Для удобства экспортируем график в html
  if save_html:
    plotly.offline.plot(fig, filename=f'fourie_data_{draw_by}.html', show_link=True)
  if draw_fig:
    fig.show()

In [ ]:
draw_fourie('max')

In [ ]:
draw_fourie('mean')

На графиках выше видно:
1. График спокойного прослушивания музыки отличается от графика ЭЭГ. В случае с ЭЭГ были виднее альфа волн.
1. График спокойного состояния показывает неидеальность снятия данных, так как нет явно выраженных альфа волн. 
1. Графики математики, программирования и игры:
  + Гарфик игры активные Бета-волны, которые однако спадают после примерно 18Гц. Вывод, игра не сильно напрягла мозг.
  +  Следую данным графика после 20 Гц программирование оказалось более напрягающей задачей и сильнее напрягло мозг.
  + В случае математических задачь. На графике видны не только небольшие Бета-волны, но и Гамма-волны, что говорит омаксимальном сосредоточении внимания.


В данной лабораторной работе графики лучше отражают работу мозга, чем в работе с ЭЭГ.

## Применяем обратное преобразование Фурье

In [ ]:
def inverse_fourie(y):
  inv=irfft(y)
  x = np.linspace(0,len(inv), len(inv))
  return {
      'x': x,
      'y': inv
  }

### Вспомогательные функции

In [ ]:
def pick(x,y,start,end):
  return [(y[i] if (x[i]>=start) & (x[i]<=end) else 0) for i in range(len(x))]

In [ ]:
def average_interpolation(data):
  interp = []
  for row in range(len(data['signals']['EXG Channel 0'])):
    interp.append(mean([data['signals'][name][row] for name in data['channels']]))
  return interp

## Изобразим график

In [ ]:
def draw_inverse_fourie(name, draw_fig = True, save_html=False):
  data = [data for data in input_data_list if data['name'] == name][0]
  index = labels.index(name)
  interp = average_interpolation(data)
  m = mean(interp)

  fig = make_subplots(
      rows=6, cols=1, subplot_titles=(['All waves'] + [wave['name'] for wave in bounds])
  )

  interp_df = pd.DataFrame({'x': np.linspace(0,len(interp),len(interp)), 'y': interp - m})
  fig.add_trace(
      go.Scatter(
        x=interp_df['x'], y=interp_df['y'], name="EEG", line = dict(width = 1)
      ), row=1, col=1
  )
  fig.update_yaxes(range=[-2,2], row=1, col=1)

  row = 1
  for wave in bounds:
    row += 1
    segment = pick(data['x'], data['y'], wave['start'], wave['end'])
    inverse_fourie_df = pd.DataFrame(inverse_fourie(segment))
    fig.add_trace(
      go.Scatter(
        x=inverse_fourie_df['x'], y=inverse_fourie_df['y'], name="EEG", line = dict(width = 1)
      ), row=row, col=1
    )
    fig.update_yaxes(range=[-2,2], row=row, col=1)

  fig.update_layout(title_text='Inverse fourie ' + name, height=len(input_data_list) * 150, showlegend=False)

  # Для удобства экспортируем график в html
  if save_html:
    plotly.offline.plot(fig, filename=f'inverse_fourie_data_{name}.html', show_link=True)
  if draw_fig:
    fig.show()

In [ ]:
draw_inverse_fourie('calm')